In [1]:
!pip install moviepy pydub


  Using cached python_dotenv-1.1.0-py3-none-any.whl.metadata (24 kB)
   ---------------------------------------- 0.0/31.2 MB ? eta -:--:--
   - -------------------------------------- 0.8/31.2 MB 3.7 MB/s eta 0:00:09
   -- ------------------------------------- 1.8/31.2 MB 5.0 MB/s eta 0:00:06
   --- ------------------------------------ 2.9/31.2 MB 4.8 MB/s eta 0:00:06
   ----- ---------------------------------- 3.9/31.2 MB 5.0 MB/s eta 0:00:06
   ------ --------------------------------- 5.2/31.2 MB 5.0 MB/s eta 0:00:06
   -------- ------------------------------- 6.3/31.2 MB 5.1 MB/s eta 0:00:05
   --------- ------------------------------ 7.6/31.2 MB 5.2 MB/s eta 0:00:05
   ---------- ----------------------------- 8.4/31.2 MB 5.3 MB/s eta 0:00:05
   ------------ --------------------------- 9.4/31.2 MB 5.0 MB/s eta 0:00:05
   ------------- -------------------------- 10.2/31.2 MB 5.0 MB/s eta 0:00:05
   ------------- -------------------------- 10.2/31.2 MB 5.0 MB/s eta 0:00:05
   ---------

  You can safely remove it manually.


In [2]:
!pip install tqdm

In [17]:
!pip install pytesseract


*TODO*

Ignorar qualquer processamento já feito antes (leve em conta o conteudo dentros dos sub_topicos, se eles existirem é porque já foram criados) se existir, deve proseguir para o proximo

In [ ]:
import subprocess
from pydub import AudioSegment, silence
import os
from tqdm import tqdm
from pathlib import Path
import shutil

# 1. Extrair o áudio usando ffmpeg
def extrair_audio_com_ffmpeg(video_path, audio_path):
    if os.path.exists(audio_path):
        print(f"[⚠️] Arquivo já existe, ignorando: {audio_path}")
        return
    
    os.makedirs(os.path.dirname(audio_path), exist_ok=True)
    
    comando = [
        "ffmpeg",
        "-i", video_path,
        "-vn",
        "-acodec", "pcm_s16le",
        "-ar", "16000",
        "-ac", "1",
        audio_path
    ]
    
    # comando = [
    #     "ffmpeg",
    #     "-loglevel", "error",
    #     "-y",
    #     "-ss", str(tempo_segundos),
    #     "-i", video_path,
    #     "-frames:v", "1",
    #     "-q:v", "2",
    #     output_imagem_path
    # ]
    subprocess.run(comando, check=True)
    print(f"[✅] Áudio extraído para: {audio_path}")

# 2. Dividir o áudio nos silêncios E registrar tempos
# def dividir_audio(audio_path, output_audio_folder, video_path, output_image_folder, min_silence_len=500, silence_thresh=-30, margem_ms=200):
def dividir_audio(audio_path, output_audio_folder, video_path, output_image_folder, min_silence_len=500, silence_thresh=-30, margem_ms=200, duracao_minima=0.5):
    audio = AudioSegment.from_wav(audio_path)

    os.makedirs(output_audio_folder, exist_ok=True)
    os.makedirs(output_image_folder, exist_ok=True)

    # Identifica os trechos de áudio entre silêncios
    silent_ranges = silence.detect_silence(
        audio,
        min_silence_len=min_silence_len,
        silence_thresh=silence_thresh
    )

    # Transformar a lista para começar e terminar onde há som
    boundaries = [0] + [item for sublist in silent_ranges for item in sublist] + [len(audio)]

    # Pega os intervalos de fala
    for i in tqdm(range(0, len(boundaries)-1, 2)):
        start = boundaries[i]
        end = boundaries[i+1]
        
        # Adiciona uma margem ao início e ao fim do áudio
        start_margem = max(start - margem_ms, 0)  # Evita ir para valores negativos
        end_margem = min(end + margem_ms, len(audio))  # Evita ultrapassar o final do áudio
        
        palavra = audio[start_margem:end_margem]

        # Verifica se a duração do áudio é maior que o mínimo definido
        if palavra.duration_seconds >= duracao_minima:
            # Salva o trecho de áudio
            palavra.export(f"{output_audio_folder}/palavra_{i//2 + 1}.wav", format="wav")

            # Calcula tempo em segundos
            tempo_medio_ms = (start + end) / 2
            tempo_medio_seg = tempo_medio_ms / 1000

            # Extrai a imagem do vídeo nesse tempo
            salvar_frame(video_path, tempo_medio_seg, f"{output_image_folder}/imagem_{i//2 + 1}.jpg")
        else:
            print(f"[⏩] Ignorando áudio pequeno com duração de {palavra.duration_seconds:.2f} segundos.")


# 3. Salvar um frame do vídeo em um tempo específico
def salvar_frame(video_path, tempo_segundos, output_imagem_path):
    comando = [
        "ffmpeg",
        "-ss", str(tempo_segundos),
        "-i", video_path,
        "-frames:v", "1",
        "-q:v", "2",  
        output_imagem_path
    ]
    subprocess.run(comando, check=True)

# 4. Exemplo de uso
def extract_data_from_videos():
    # Caminhos base
    video_dir = Path("data/video")
    audio_template = "data/audio/original/{topico}/{sub_topico}/audio_extraido.wav"
    output_audio_template = "data/audio/chunk/{topico}/{sub_topico}"
    output_image_template = "data/image/extract_to_video/{topico}/{sub_topico}"

    # Itera sobre vídeos
    for video_file in video_dir.glob("*.mp4"):
        try:
            # Extrai nome sem extensão e separa tópicos
            video_name = video_file.stem.replace(".mp4", "")  # remove .mp4
            topico, sub_topico = video_name.split("__")

            print(f"🎥 Processando vídeo: {video_file.name}")
            print(f"📁 Tópico: {topico} | Subtópico: {sub_topico}")

            # Prepara caminhos
            audio_path = Path(audio_template.format(topico=topico, sub_topico=sub_topico))
            output_audio_folder = Path(output_audio_template.format(topico=topico, sub_topico=sub_topico))
            output_image_folder = Path(output_image_template.format(topico=topico, sub_topico=sub_topico))

            # Cria pastas de saída se não existirem
            output_audio_folder.mkdir(parents=True, exist_ok=True)
            output_image_folder.mkdir(parents=True, exist_ok=True)

            # Processa
            extrair_audio_com_ffmpeg(video_file, audio_path)
            dividir_audio(audio_path, output_audio_folder, video_file, output_image_folder)

        except Exception as e:
            print(f"❌ Erro ao processar {video_file.name}: {e}")

    print("✅ Finalizado!")

extract_data_from_videos()


🎥 Processando vídeo: pessoas__identidade.mp4
📁 Tópico: pessoas | Subtópico: identidade


ffmpeg version 6.1.1-3ubuntu5 Copyright (c) 2000-2023 the FFmpeg developers
  built with gcc 13 (Ubuntu 13.2.0-23ubuntu3)
  configuration: --prefix=/usr --extra-version=3ubuntu5 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --disable-omx --enable-gnutls --enable-libaom --enable-libass --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libglslang --enable-libgme --enable-libgsm --enable-libharfbuzz --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-libzimg --ena

[✅] Áudio extraído para: data/audio/original/pessoas/identidade/audio_extraido.wav


  0%|          | 0/25 [00:00<?, ?it/s]ffmpeg version 6.1.1-3ubuntu5 Copyright (c) 2000-2023 the FFmpeg developers
  built with gcc 13 (Ubuntu 13.2.0-23ubuntu3)
  configuration: --prefix=/usr --extra-version=3ubuntu5 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --disable-omx --enable-gnutls --enable-libaom --enable-libass --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libglslang --enable-libgme --enable-libgsm --enable-libharfbuzz --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx265 --enable-libxml2 -

[⏩] Ignorando áudio pequeno com duração de 0.20 segundos.


...

[⏩] Ignorando áudio pequeno com duração de 0.20 segundos.


ffmpeg version 6.1.1-3ubuntu5 Copyright (c) 2000-2023 the FFmpeg developers
  built with gcc 13 (Ubuntu 13.2.0-23ubuntu3)
  configuration: --prefix=/usr --extra-version=3ubuntu5 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --disable-omx --enable-gnutls --enable-libaom --enable-libass --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libglslang --enable-libgme --enable-libgsm --enable-libharfbuzz --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libtheora --enable-libtwolame --enable-libvidstab --enable-libvorbis --enable-libvpx --enable-libwebp --enable-libx265 --enable-libxml2 --enable-libxvid --enable-libzimg --ena

[⏩] Ignorando áudio pequeno com duração de 0.46 segundos.


[swscaler @ 0x6106941a84c0] deprecated pixel format used, make sure you did set range correctly
    Last message repeated 2 times
Output #0, image2, to 'data/image/extract_to_video/casa/tipos_de_casa/imagem_13.jpg':
  Metadata:
    major_brand     : mp42
    minor_version   : 0
    compatible_brands: isommp42
    com.android.version: 14
    encoder         : Lavf60.16.100
  Stream #0:0(eng): Video: mjpeg, yuvj420p(pc, bt470bg/bt470bg/smpte170m, progressive), 1080x2340, q=2-31, 200 kb/s, 15.19 fps, 15.19 tbn (default)
    Metadata:
      creation_time   : 2025-04-29T23:11:33.000000Z
      handler_name    : VideoHandle
      vendor_id       : [0][0][0][0]
      encoder         : Lavc60.31.102 mjpeg
    Side data:
      cpb: bitrate max/min/avg: 0/0/200000 buffer size: 0 vbv_delay: N/A
[image2 @ 0x610693a4e500] The specified filename 'data/image/extract_to_video/casa/tipos_de_casa/imagem_13.jpg' does not contain an image sequence pattern or a pattern is invalid.
[image2 @ 0x610693a4e500] 

[⏩] Ignorando áudio pequeno com duração de 0.20 segundos.
✅ Finalizado!


---

In [50]:
# import os
# import subprocess

# def extrair_audio_com_ffmpeg(video_path, audio_path):
#     # Cria o diretório se não existir
#     os.makedirs(os.path.dirname(audio_path), exist_ok=True)
    
#     # Executa o comando ffmpeg
#     comando = [
#         "ffmpeg",
#         "-i", video_path,
#         "-vn",              
#         "-acodec", "pcm_s16le",  
#         "-ar", "16000",     
#         "-ac", "1",         
#         audio_path
#     ]
#     subprocess.run(comando, check=True)

# # Caminho do vídeo
# video_file = "/media/guilherme/ssd_m2_data/py_new_projects/fast_english/extract_data_video/data/video/topico_2__sub_topico_2.mp4"

# # Extrair nome do arquivo e obter tópicos
# basename = os.path.basename(video_file).replace(".mp4", "")
# topico, sub_topico = basename.split("__")

# # Caminho para salvar o áudio
# audio_path = f"data/audio/{topico}/{sub_topico}/audio_extraido.wav"

# # Chamada da função
# extrair_audio_com_ffmpeg(video_file, audio_path)


In [25]:
import cv2
import json
from pathlib import Path

def save_json_rects_to_crop():
    retangulos = []
    ponto_inicial = None

    # Caminho da imagem
    caminho_imagem = Path("data/palavras_extraidas_imagem/imagem_36.jpg")
    nome_imagem = caminho_imagem.stem
    output_json = caminho_imagem.with_name(f"retangulos_corte_imagem.json")

    # Carrega imagem e redimensiona
    img = cv2.imread(str(caminho_imagem))
    if img is None:
        print(f"❌ Erro ao carregar imagem: {caminho_imagem}")
        return

    escala = 0.4
    img_mini = cv2.resize(img, (int(img.shape[1] * escala), int(img.shape[0] * escala)))

    # Callback de clique
    def clique(event, x, y, flags, param):
        nonlocal ponto_inicial
        if event == cv2.EVENT_LBUTTONDOWN:
            if ponto_inicial is None:
                ponto_inicial = (x, y)
                print(f"🟢 Primeiro ponto: {ponto_inicial}")
            else:
                ponto_final = (x, y)
                print(f"🔴 Segundo ponto: {ponto_final}")
                x1, y1 = ponto_inicial
                x2, y2 = ponto_final
                retangulos.append((x1, y1, x2, y2))
                cv2.rectangle(img_mini, (x1, y1), (x2, y2), (0, 255, 0), 2)
                cv2.imshow("Imagem", img_mini)
                ponto_inicial = None

    # Interface gráfica
    cv2.imshow("Imagem", img_mini)
    cv2.setMouseCallback("Imagem", clique)
    print("🖱️ Clique dois pontos para cada retângulo (canto sup. esquerdo e inf. direito). Pressione 'q' para sair.")

    while True:
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cv2.destroyAllWindows()

    # Salva os retângulos no JSON
    with open(output_json, "w") as f:
        json.dump(retangulos, f)
    print(f"✅ {len(retangulos)} retângulo(s) salvo(s) em {output_json}")

# Exemplo de uso
if __name__ == "__main__":
    save_json_rects_to_crop()


❌ Erro ao carregar imagem: data/palavras_extraidas_imagem/imagem_36.jpg


[ WARN:0@0.018] global loadsave.cpp:268 findDecoder imread_('data/palavras_extraidas_imagem/imagem_36.jpg'): can't open/read file: check file path/integrity


In [ ]:
# TODO: how to pronounce myopia -> mai·ow·pee·uh


In [58]:
import cv2
import json
from pathlib import Path
import numpy as np

from PIL import Image
import pytesseract

# Parâmetros globais
ESCALA = 0.4
PASTA_IMAGENS = Path("data/image/extract_to_video")
PASTA_JSON_RETANGULOS_CORTE = Path("data/json/retangulos_corte_imagem.json")
PASTA_SAIDA = Path("data/recortes")


def extrair_texto_de_imagem(caminho_imagem, lang='eng'):
    """
    sudo apt install tesseract-ocr-por
    pip install pytesseract pillow
    sudo apt install tesseract-ocr
    """
    imagem = Image.open(caminho_imagem)
    texto = pytesseract.image_to_string(imagem, lang=lang)
    return texto.strip()


def save_json(json_path, dict_text):
    # Salva o dicionário como JSON
    with open(json_path, "w", encoding="utf-8") as f:
        json.dump(dict_text, f, indent=2, ensure_ascii=False)
        
def resize_frame(frame, escala=ESCALA):
    altura, largura = frame.shape[:2]
    nova_largura = int(largura * escala)
    nova_altura = int(altura * escala)
    return cv2.resize(frame, (nova_largura, nova_altura))

def processar_imagem(caminho_imagem: Path):
    nome_arquivo = caminho_imagem.stem  # Ex: imagem_42
    json_path = PASTA_JSON_RETANGULOS_CORTE

    if not json_path.exists():
        print(f"⚠️ JSON não encontrado para {caminho_imagem.name}")
        return

    img = cv2.imread(str(caminho_imagem))
    if img is None:
        print(f"❌ Erro ao carregar imagem: {caminho_imagem}")
        return

    with open(json_path, "r") as f:
        retangulos = json.load(f)

    if not retangulos:
        print(f"❌ Nenhum retângulo em {json_path}")
        return

    # Caminho de saída preservando a estrutura
    estrutura_relativa = caminho_imagem.relative_to(PASTA_IMAGENS).parent
    pasta_destino = PASTA_SAIDA / estrutura_relativa / nome_arquivo
    pasta_destino.mkdir(parents=True, exist_ok=True)

    # Redimensiona imagem
    # img_resize = resize_frame(img)
    dict_text = {}

    for i, (x1, y1, x2, y2) in enumerate(retangulos):
        x1, x2 = sorted([x1, x2])
        y1, y2 = sorted([y1, y2])

        # Corrige coordenadas com base na escala original
        x1 = int(x1 / ESCALA)
        x2 = int(x2 / ESCALA)
        y1 = int(y1 / ESCALA)
        y2 = int(y2 / ESCALA)

        recorte = img[y1:y2, x1:x2]

        image_name = f"recorte_{i}.jpg"
        caminho_recorte = os.path.join(pasta_destino, image_name)
        
        cv2.imwrite(str(caminho_recorte), recorte)
        # print(f"✅ Recorte salvo: {caminho_recorte}")

        if i != 0:
            if i == 1:
                texto = extrair_texto_de_imagem(caminho_recorte, lang="por")
            else:
                texto = extrair_texto_de_imagem(caminho_recorte, lang="por")

            dict_text.update({image_name:texto})
            # print(f"📝 Texto extraído: {texto}")
        
        
   # Ao final, o dict_text contém os textos dos recortes (exceto o primeiro)
    print("📄 Dicionário final de textos extraídos:")
    json_path = os.path.join(pasta_destino, "text.json")
    save_json(json_path=json_path, dict_text=dict_text)

# Procura todas as imagens dentro dos tópicos/subtópicos
list_path_imgs = PASTA_IMAGENS.rglob("*.jpg")
for caminho_imagem in tqdm(list_path_imgs, total=len(list_path_imgs)):
    processar_imagem(caminho_imagem)


✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_13/recorte_0.jpg
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_13/recorte_1.jpg
📝 Texto extraído: a alcunha
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_13/recorte_2.jpg
📝 Texto extraído: Nome Sinaular
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_13/recorte_3.jpg
📝 Texto extraído: nickname
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_13/recorte_4.jpg
📝 Texto extraído: /nikneim/
📄 Dicionário final de textos extraídos:
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_8/recorte_0.jpg
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_8/recorte_1.jpg
📝 Texto extraído: a senhora
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_8/recorte_2.jpg
📝 Texto extraído: Nome Sinaular
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_8/recorte_3.jpg
📝 Texto extraído: missus
✅ Recorte salvo: data/recortes/pessoas/identidade/imagem_8/recorte_4.jpg
📝 Texto extraído: /miIsIz

---

In [55]:
# Arganiza pastas com arquivos repetidos

import os
import json
import shutil

def ler_json(caminho):
    with open(caminho, 'r', encoding='utf-8') as f:
        return json.load(f)

def organizar_unicos(base_path):
    traducoes_unicas = {}  # chave = (pt, en), valor = caminho da primeira imagem encontrada

    for topico in os.listdir(base_path):
        path_topico = os.path.join(base_path, topico)

        if not os.path.isdir(path_topico):
            continue

        for subtopico in os.listdir(path_topico):
            path_subtopico = os.path.join(path_topico, subtopico)

            if not os.path.isdir(path_subtopico):
                continue

            imagens = sorted(os.listdir(path_subtopico))  # para manter ordem
            vistos = {}

            for imagem in imagens:
                path_imagem = os.path.join(path_subtopico, imagem)
                path_json = os.path.join(path_imagem, "text.json")

                if not os.path.isdir(path_imagem) or not os.path.exists(path_json):
                    continue

                dados = ler_json(path_json)
                chave = (dados.get("pt"), dados.get("en"))

                if chave in vistos:
                    # Duplicado, deletar a pasta atual
                    print(f"Removendo duplicado: {path_imagem}")
                    # shutil.rmtree(path_imagem)
                else:
                    vistos[chave] = path_imagem

            print(f"[✓] Subtópico '{subtopico}' do tópico '{topico}' processado.")

# 🟢 Use assim:
organizar_unicos("data/recortes")


Removendo duplicado: data/recortes/pessoas/familia/imagem_11
Removendo duplicado: data/recortes/pessoas/familia/imagem_12
Removendo duplicado: data/recortes/pessoas/familia/imagem_13
Removendo duplicado: data/recortes/pessoas/familia/imagem_14
Removendo duplicado: data/recortes/pessoas/familia/imagem_15
Removendo duplicado: data/recortes/pessoas/familia/imagem_16
Removendo duplicado: data/recortes/pessoas/familia/imagem_17
Removendo duplicado: data/recortes/pessoas/familia/imagem_18
Removendo duplicado: data/recortes/pessoas/familia/imagem_19
Removendo duplicado: data/recortes/pessoas/familia/imagem_2
Removendo duplicado: data/recortes/pessoas/familia/imagem_20
Removendo duplicado: data/recortes/pessoas/familia/imagem_21
Removendo duplicado: data/recortes/pessoas/familia/imagem_22
Removendo duplicado: data/recortes/pessoas/familia/imagem_23
Removendo duplicado: data/recortes/pessoas/familia/imagem_24
Removendo duplicado: data/recortes/pessoas/familia/imagem_25
Removendo duplicado: data

In [78]:
list_text = {}

list_text.update({"teste":"ok"})
list_text.update({"teste2":"ok"})


list_text

{'teste': 'ok', 'teste2': 'ok'}

In [62]:
import numpy as np

In [46]:
# type(img)

True

In [52]:
caminho_imagem = r"data\image\extract_to_video\topico_1\sub_topico_1\imagem_42.jpg"
img = cv2.imread(caminho_imagem)

if img is None:
    print("❌ Nenhum imagem encontrada.")